In [1]:
import numpy as np
import pandas as pd

import torch

from gaussian_ring_grid_generator import GaussianRingSpaceTimeGrid
import encoder
import importlib
import viz_mfsr
# from viz_mfsr import *
importlib.reload(encoder)
importlib.reload(viz_mfsr)

<module 'viz_mfsr' from '/home/ns4486/repos/numerical-relativity-interpolation/dev/encoder_sr/viz_mfsr.py'>

In [2]:
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')

In [3]:
spaceTimeContext = GaussianRingSpaceTimeGrid(
    n_space_grid = 32,
    n_time_grid = 5,
    space_min_x = -5,
    space_max_x = 5,
    time_min_t = 0.5,
    time_max_t = 2.5
)


# spaceTimeContext = GaussianRingSpaceTimeGrid(
#     n_space_grid = 32,
#     n_time_grid = 5,
#     space_min_x = -5,
#     space_max_x = 5,
#     time_min_t = 0.3,
#     time_max_t = 2.3
# )

/home/ns4486/repos/numerical-relativity-interpolation/dev/encoder_sr/gaussian_ring_grid_generator.py:36: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  [torch.tensor(GaussianRing(self.space_grid.cpu(), i, i/2)).unsqueeze(0) for i in self.time_axis]


In [4]:
test_grid = GaussianRingSpaceTimeGrid(
    n_space_grid = 48,
    n_time_grid = 5,
    space_min_x = -5,
    space_max_x = 5,
    time_min_t = 0.75,
    time_max_t = 2.25
)

# test_grid = GaussianRingSpaceTimeGrid(
#     n_space_grid = 64,
#     n_time_grid = 6,
#     space_min_x = -4.5,
#     space_max_x = 4.5,
#     time_min_t = 0.75,
#     time_max_t = 2.25
# )

In [5]:
test_grid.time_axis

tensor([0.7500, 1.1250, 1.5000, 1.8750, 2.2500], device='cuda:0')

In [6]:
def get_decimal_index(axis_values, value):
    closest_above = axis_values[axis_values >= value].min()
    closest_below = axis_values[axis_values <= value].max()
    index_below = np.where(axis_values == closest_below)[0][0]
    
    if closest_above == closest_below:
        return index_below
    
    return index_below + ((value - closest_below)/(closest_above - closest_below))

In [7]:
ts = []
xs = []
ys = []
zs = []

time_t = []
space_x = []
space_y = []
space_z = []

vals = []
time_indices = []

for i in range(test_grid.values.shape[0]):
# for i in [0]:
    t = get_decimal_index(spaceTimeContext.time_axis.cpu().numpy(), test_grid.time_axis[i].item())
    
    
    for j in range(test_grid.values.shape[2]):
        x = get_decimal_index(spaceTimeContext.space_axis.cpu().numpy(), test_grid.space_axis[j].item())
        
        
        for k in range(test_grid.values.shape[3]):
            y = get_decimal_index(spaceTimeContext.space_axis.cpu().numpy(), test_grid.space_axis[k].item())
            
            
            for l in range(test_grid.values.shape[4]):
                z = get_decimal_index(spaceTimeContext.space_axis.cpu().numpy(), test_grid.space_axis[l].item())
                
                ts.append(t)
                xs.append(x)
                ys.append(y)
                zs.append(z)
                
                time_t.append(test_grid.time_axis[i].item())
                space_x.append(test_grid.space_axis[j].item())
                space_y.append(test_grid.space_axis[k].item())
                space_z.append(test_grid.space_axis[l].item())
                time_indices.append(i)
                
                vals.append(test_grid.values[i, 0, j, k, l].item())

In [8]:
test_grid.values.shape[0]

5

In [9]:
inps = np.array([ts, xs, ys, zs]).T
outs = np.array(vals)
inps.shape, outs.shape

((552960, 4), (552960,))

In [10]:
input_tensor = torch.Tensor(inps).unsqueeze(1)
output_tensor = torch.Tensor(outs).unsqueeze(1)
input_tensor.shape, output_tensor.shape

(torch.Size([552960, 1, 4]), torch.Size([552960, 1]))

In [11]:
from torch.utils.data import TensorDataset, DataLoader

test_dataset = TensorDataset(input_tensor,output_tensor) # create your datset
test_dataloader = DataLoader(test_dataset, batch_size=32768)

In [12]:
import torch.nn as nn

model = encoder.SR(1, 16, 5)

In [23]:
model.load_state_dict(torch.load('/scratch/ns4486/capstone/checkpoints/encoder_sr/conf2_epoch=2500.pt'))

<All keys matched successfully>

In [24]:
import tqdm

model.to(device)
model.eval()

outputs = []

running_loss = 0.0
for i, data in tqdm.tqdm(enumerate(test_dataloader, 0)):
    # get the inputs; data is a list of [inputs, labels]
    inputs, labels = data

    inputs = inputs.to(device)
    labels = labels.to(device)

    # forward + backward + optimize
    with torch.no_grad():
        output = model(spaceTimeContext.values, inputs)
#         print(inputs)
#         print(labels)
#     print(outputs.shape)
    
    outputs.append(output)


17it [00:07,  2.13it/s]


In [25]:
outputs[0].shape

torch.Size([32768, 1])

In [26]:
model_outputs = torch.cat(outputs, dim=0).squeeze(1).detach().cpu().numpy()

In [27]:
df = pd.DataFrame(list(zip(time_indices, space_x, space_y, space_z, vals, list(model_outputs))), columns =['t', 'x', 'y', 'z', 'expected', 'predicted']) 

In [28]:
df['z'].unique(), df['t'].unique()

(array([-5.        , -4.78723383, -4.57446814, -4.36170197, -4.14893627,
        -3.9361701 , -3.72340417, -3.51063824, -3.2978723 , -3.08510637,
        -2.87234044, -2.65957451, -2.44680858, -2.23404264, -2.02127671,
        -1.80851066, -1.59574473, -1.38297868, -1.17021275, -0.95744681,
        -0.74468082, -0.53191489, -0.31914893, -0.10638298,  0.10638298,
         0.31914893,  0.53191489,  0.74468082,  0.95744681,  1.17021275,
         1.38297868,  1.59574473,  1.80851066,  2.02127671,  2.23404264,
         2.44680858,  2.65957451,  2.87234044,  3.08510637,  3.2978723 ,
         3.51063824,  3.72340417,  3.9361701 ,  4.14893627,  4.36170197,
         4.57446814,  4.78723383,  5.        ]),
 array([0, 1, 2, 3, 4]))

In [29]:
# df = df[(np.isclose(df['t'], 0.75)) & (np.isclose(df['z'], 0.74468082))]
df = df[(np.isclose(df['z'], 0.74468082))]
df_exp = df.drop(['predicted', 'z'], axis = 1)
df_pred = df.drop(['expected', 'z'], axis = 1)

df_exp = df_exp.rename(columns = {'expected': 'z'})
df_pred = df_pred.rename(columns = {'predicted': 'z'})

df_exp['bool_predicted'] = 0
df_pred['bool_predicted'] = 1

df_viz = pd.concat([df_exp, df_pred])
df_viz = df_viz.rename(columns = {'t' : 'time'})
# df_viz['time'] = 0

In [30]:
viz_mfsr.plot_gaussian_ring(df_viz, time_index = 0)

In [31]:
viz_mfsr.plot_residual_ring(df_viz)

In [32]:
viz_mfsr.animate_gaussian_ring(df_viz)

In [34]:
viz_mfsr.plot_gaussian_ring(df_viz, time_index = 2)

In [33]:
viz_mfsr.plot_residual_ring(df_viz, time_index = 2)

In [ ]:
df[(np.isclose(df['t'], 1.64999998)) & (np.isclose(df['z'], 0.07142857))]

In [ ]:
df['residual'] = df['expected'] - df['predicted']

In [ ]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

In [ ]:
subset = df[(np.isclose(df['t'], 0.75)) & (np.isclose(df['z'], 0.74468082))]

In [ ]:
fig = make_subplots(rows=1, cols=2)

fig.add_trace(
    go.Scatter(x=subset['x'], y=subset['y'], mode = 'markers', marker=dict(
        color=subset['expected'],
        size=12,
        cmin = 0,
        cmax = 1.063488245010376
    )),
    row=1, col=1
)

fig.show()

In [ ]:
# subset = df[(np.isclose(df['t'], 1.86999989)) & (np.isclose(df['z'], 0.48387095))]
fig = make_subplots(rows=1, cols=2)

fig.add_trace(
    go.Scatter(x=subset['x'], y=subset['y'], mode = 'markers', marker=dict(
        color=subset['predicted'],
        size=12,
        cmin = 0,
        cmax = 1.063488245010376
    )),
    row=1, col=1
)

fig.show()

In [ ]:
fig = make_subplots(rows=1, cols=2)

fig.add_trace(
    go.Scatter(x=subset['x'], y=subset['y'], mode = 'markers', marker=dict(
        color=subset['residual'],
        size=12,
        cmin = -1.063488245010376,
        cmax = 1.063488245010376
    )),
    row=1, col=1
)

fig.show()

In [ ]:
subset['expected'].min(), subset['expected'].max(), subset['expected'].mean(), subset['expected'].std()

In [ ]:
subset['predicted'].min(),subset['predicted'].max(),subset['predicted'].mean(),subset['predicted'].std()

In [ ]:
subset['residual'].min(),subset['residual'].max(),subset['residual'].mean(),subset['residual'].std()

In [ ]:
import seaborn as sns
import matplotlib.pyplot as plt
plt.figure(figsize = (20, 12))
x = subset['residual']

# threshold = 0.1
# x = x[(x < -threshold) | (x > threshold)]
sns.distplot(x, kde = False)

In [ ]:
import matplotlib.pyplot as plt

plt.hist(subset['expected'], bins=100)

In [ ]:
plt.hist(subset['predicted'], bins=100)